# Hotel Data Processing


In [1]:
import pandas as pd
import numpy as np
from datetime import datetime
import requests
"""
16	Acapulco
10	Bahía Huatulco
15	Cancún
8	Corredor Los Cabos
12	Ensenada
17	Isla Mujeres
14	La Paz
6	Los Cabos
1	Mazatlán
4	Mérida
9	Playa del Carmen
11	Puerto Escondido
2	Puerto Vallarta
5	Riviera Nayarit
7	San José del Cabo
13	San Miguel de Allende
18	Tulum
3	Veracruz
"""

checkin_date = datetime.now().strftime("%Y-%m-%d")
# checkin_date = '2025-12-06'

# Cargar archivo
df = pd.read_csv(f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Proyectos/Precio por noche Hoteles/Hoteles_PriceTravel/Hoteles_PriceTravel_{checkin_date}.csv")
# Limpia precios y convierte a float
#df['precio_float'] = df['precios'].str.replace('$', '').str.replace('MXN', '').str.replace(',', '').astype(float)
# Redondea estrellas
df['estrellas_redondeadas'] = df['estrellas'].apply(lambda x: np.floor(x + 0.5) if pd.notna(x) else np.nan)
# Agrupa por ciudad y calcula promedios
df_total = df.groupby('ciudad')['precios'].mean().reset_index(name='prom_total').round()
df_4 = df[df['estrellas_redondeadas'] == 4].groupby('ciudad')['precios'].mean().reset_index(name='prom_4_estrellas').round()
df_5 = df[df['estrellas_redondeadas'] == 5].groupby('ciudad')['precios'].mean().reset_index(name='prom_5_estrellas').round()

# Une todo en un solo DataFrame final
df_final = df_total.merge(df_4, on='ciudad', how='left').merge(df_5, on='ciudad', how='left')

# Guardar resultados
df_final.to_csv(f"Hoteles_resumen_mxn_dls/Hoteles_resumen_{checkin_date}.csv", index=False, encoding='utf-8-sig')

df_final



ciudad  prom_total  prom_4_estrellas  prom_5_estrellas
0                Acapulco      1439.0            1925.0               NaN
1          Bahía Huatulco      3262.0            4246.0            4721.0
2                  Cancún      5205.0            4730.0           10294.0
3      Corredor Los Cabos     15033.0            8081.0           18328.0
4                Ensenada      2967.0            2994.0            6212.0
5            Isla Mujeres      8622.0            7374.0           12454.0
6                  La Paz      3160.0            5043.0               NaN
7               Los Cabos     10291.0            5487.0           18797.0
8                Mazatlán      1861.0            1795.0            5283.0
9                  Mérida      2015.0            2732.0            3980.0
10       Playa del Carmen      5282.0            2638.0           13514.0
11       Puerto Escondido      3029.0            5521.0               NaN
12        Puerto Vallarta      5284.0            4457.0           10555.0
13        Riviera Nayarit      6925.0            5017.0           14242.0
14      San José del Cabo     12778.0            5497.0           23864.0
15  San Miguel de Allende      3270.0            3538.0            6922.0
16                  Tulum      9691.0           14505.0           10197.0
17               Veracruz      1300.0            1659.0            3693.0

In [2]:
# Código para obtener el precio del dólar hoy (USD a MXN)



# Para obtener el tipo de cambio en una fecha específica:

def obtener_precio_dolar_fecha(fecha='2024-06-27'):
    url = f"https://api.exchangerate.host/{fecha}?base=USD&symbols=MXN"
    response = requests.get(url)

    if response.status_code == 200:
        data = response.json()
        precio = data["rates"]["MXN"]
        print(f"💵 El precio del dólar el {fecha} fue: {precio:.2f}")
        return precio
    else:
        print("❌ Error al consultar el tipo de cambio")
        return None

# Ejemplo
# obtener_precio_dolar_fecha("2025-11-03")



def obtener_precio_dolar():
    url = "https://api.exchangerate-api.com/v4/latest/USD"  # Asegúrate de que esta URL sea correcta
    response = requests.get(url)
    
    if response.status_code == 200:
        data = response.json()
        if "rates" in data and "MXN" in data["rates"]:
            precio = data["rates"]["MXN"]
            print(f"💵 El precio del dólar hoy (USD -> MXN) es: {precio:.2f}")
            return precio
        else:
            print("❌ La respuesta no contiene la clave 'rates' o 'MXN'.")
            print("Respuesta completa:", data)
            return None
    else:
        print(f"❌ Error al consultar la API. Código de estado: {response.status_code}")
        return None

# Ejecutar
obtener_precio_dolar()


💵 El precio del dólar hoy (USD -> MXN) es: 17.91


17.91

In [3]:
# Obtener el tipo de cambio actual (ejemplo: desde una API o valor fijo)
import io
import sys

# Redirigir salida estándar temporalmente
stdout_backup = sys.stdout
sys.stdout = io.StringIO()

TIPO_DE_CAMBIO = obtener_precio_dolar()

# Restaurar salida estándar
sys.stdout = stdout_backup

# Mostrar solo el valor
TIPO_DE_CAMBIO

# Convertir precios a dólares
df_final_dolar = df_final.copy()
columnas_a_convertir = ['prom_total', 'prom_4_estrellas', 'prom_5_estrellas']

for columna in columnas_a_convertir:
    if columna in df_final_dolar.columns:
        df_final_dolar[columna] = (df_final_dolar[columna] / TIPO_DE_CAMBIO).round(2)

# Guardar el DataFrame convertido a un archivo CSV
nombre_archivo_dolares = f"Hoteles_resumen_mxn_dls/Hoteles_resumen_{checkin_date}_dolares.csv"
df_final_dolar.to_csv(nombre_archivo_dolares, index=False, encoding='utf-8-sig')

df_final_dolar

ciudad  prom_total  prom_4_estrellas  prom_5_estrellas
0                Acapulco       80.35            107.48               NaN
1          Bahía Huatulco      182.13            237.07            263.60
2                  Cancún      290.62            264.10            574.76
3      Corredor Los Cabos      839.36            451.20           1023.34
4                Ensenada      165.66            167.17            346.85
5            Isla Mujeres      481.41            411.73            695.37
6                  La Paz      176.44            281.57               NaN
7               Los Cabos      574.60            306.37           1049.53
8                Mazatlán      103.91            100.22            294.97
9                  Mérida      112.51            152.54            222.22
10       Playa del Carmen      294.92            147.29            754.55
11       Puerto Escondido      169.12            308.26               NaN
12        Puerto Vallarta      295.03            248.86            589.34
13        Riviera Nayarit      386.66            280.12            795.20
14      San José del Cabo      713.46            306.92           1332.44
15  San Miguel de Allende      182.58            197.54            386.49
16                  Tulum      541.09            809.88            569.35
17               Veracruz       72.59             92.63            206.20